# Taxi Driver Program
Reinforcement Learning algorithm that solves the Taxi-v3 environment from OpenAI gym library

### Two possible modes:
1. User mode: Input parameters to play with optimization
2. Time mode: Input time for algorithm to find a solution

## Functionality
Run all cells, and then go to Program Frontend heading to run desired game mode.
Each mode contains instructions in documentation string

## Training

In [1]:
import gym
import numpy as np
import random
import pandas as pd
import torch
import plotly.express as px

In [2]:
env = gym.make('Taxi-v3')
env.reset()
env.render()
action_size = env.action_space.n
state_size = env.observation_space.n

+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+



In [3]:
# DEFAULT PARAMS
TOTAL_TEST_EP = 100
TOTAL_EP = 1500
MAX_STEPS = 100
LR = 0.97
GAMMA = 0.95
EPSILON = 0.95
MAX_EPSILON = 1.0
MIN_EPSILON = 0.01
DECAY_RATE = 0.01
Q_TABLE = np.zeros((state_size, action_size))


In [4]:
# MODEL INFERENCE RESULTS
rewards_total = []
steps_total = []
penalties_per_ep_total = []
timestep_per_ep_total = []

# MODEL TRAINING RESULTS
train_rewards_per_ep_total = []
train_penalties_per_ep_total = []
train_timestep_per_ep_total = []

# MODEL EVALUATION METRICS
reward_zero_crossing_point = []
max_cost = []


# Q table
q_table = np.zeros((state_size, action_size))

In [5]:
def moving_average(a, n=3) :
    ret = np.cumsum(a, dtype=float)
    ret[n:] = ret[n:] - ret[:-n]
    return ret[n - 1:] / n

def show_run_stats(rewards, penalties, steps, timesteps):
    # Rewards over episodes
    plt.figure(figsize=(12,5))
    plt.title("Rewards over episodes")
    plt.bar(torch.arange(len(rewards)), rewards, alpha=0.6, color='green', width=5)
    ma = moving_average(rewards, n=15)
    plt.plot(torch.arange(len(ma)), ma)
    # plt.plot()
    plt.show()

    plt.figure(figsize=(12,5))
    plt.title("Steps over episode")
    # plt.bar(torch.arange(len(steps_total)), steps_total, alpha=0.6, color='red', width=5)
    plt.bar(torch.arange(len(steps)), steps)
    plt.show()

    plt.figure(figsize=(12,5))
    plt.title("Penalties per episode")
    plt.plot(torch.arange(len(penalties)), penalties)
    plt.show()

    plt.figure(figsize=(12,5))
    plt.title("Timestep per episode")
    # plt.bar(torch.arange(len(steps_total)), steps_total, alpha=0.6, color='red', width=5)
    plt.plot(torch.arange((len(timesteps))), timesteps)
    plt.show()

In [6]:
def calculate_q_table(
    total_ep = TOTAL_EP,
    max_steps = MAX_STEPS,
    lr = LR,
    gamma = GAMMA,
    epsilon = EPSILON,
    max_epsilon = MAX_EPSILON,
    min_epsilon = MIN_EPSILON,
    decay_rate = DECAY_RATE,
    q_table = Q_TABLE
):
    '''
    Run training on taxi env to calculate Q-table
    :param total_ep:
    :param max_steps:
    :param lr:
    :param gamma:
    :param epsilon:
    :param max_epsilon:
    :param min_epsilon:
    :param decay_rate:
    :return:
    '''
    global train_rewards_per_ep_total
    global train_penalties_per_ep_total
    global train_timestep_per_ep_total
    global max_cost
    # global reward_zero_crossing_point
    train_rewards_per_ep_total = []
    train_penalties_per_ep_total = []
    train_timestep_per_ep_total = []
    max_cost = 0
    # reward_zero_crossing_point = 0

    for episode in range(total_ep):

        # Reset Environment:
        state = env.reset()
        step = 0
        done = False

        total_penalties_in_episode = 0
        total_rewards_in_episode = 0

        for step in range(max_steps):

            # Choose an action a in the current world state(s) (step 3)
            # First we randomize a number
            exp_exp_tradeoff = random.uniform(0, 1)

            # If this number > greater than epsilon --> exploitation (taking the biggest q value for the current state):
            if exp_exp_tradeoff > epsilon:
                action = np.argmax(q_table[state, :])

            # Else, doing random choice:
            else:
                action = env.action_space.sample()

            # Take the action (a) and observe the outcome state (s') and the reward (r)
            new_state, reward, done, info = env.step(action)

            if reward == -10:
                total_penalties_in_episode += 1

            if reward < max_cost:
                max_cost = reward


            total_rewards_in_episode += reward

            # Update Q(s,a):= Q(s,a) + lr [R(s,a) + gamma * max Q(s',a') - Q(s,a)]
            q_table[state, action] = q_table[state, action] + lr * (reward + gamma *
                                            np.max(q_table[new_state, :]) - q_table[state, action])

            # Our new state:
            state = new_state

            # If done True, finish the episode:
            if done:
                train_rewards_per_ep_total.append(total_rewards_in_episode)
                train_penalties_per_ep_total.append(total_penalties_in_episode)
                train_timestep_per_ep_total.append(step)
                break

          # Increment number of episodes:
          episode += 1

          # Reduce epsilon (because we need less and less exploration):
          epsilon = min_epsilon + (max_epsilon - min_epsilon) *np.exp(-decay_rate*episode)

    return train_rewards_per_ep_total, train_timestep_per_ep_total, train_penalties_per_ep_total, max_cost

## Optimization

In [7]:
def gridsearch(lr_range, gamma_range, epsilon_range):
    '''
    Run a gridsearch on Q-Learning to output best combination
    :param lr_range: range to test learning rate
    :param gamma_range: range to test gamma
    :param epsilon_range: range to test epsilon
    :return:
    '''
    results = pd.DataFrame()

    for lr in lr_range:
        for gamma in gamma_range:
            for epsilon in epsilon_range:
                rewards, timestep, penalties, cost = calculate_q_table(
                    lr=lr,
                    gamma=gamma,
                    epsilon=epsilon
                )
                results_ = pd.DataFrame({
                    'learning_rate':  float(lr),
                    'gamma':  float(gamma),
                    'epsilon':  float(epsilon),
                    'rewards': rewards,
                    'timesteps':  timestep,
                    'penalties':  penalties,
                    'cost':  cost,
                })
                
                results = results.append(results_)

    # index -> episode
    results = results.reset_index().rename(columns={'index': 'episode'})

    # add column with the 2 hyper-parameters
    results['hyperparameters'] = [f'lr={l}, gamma={g}, epsilon={e}' for (l, g, e) in zip(results['learning_rate'], results['gamma'], results['epsilon'])]

    print(results.head())


    return results

In [13]:
optimized_data = gridsearch(
    lr_range=np.linspace(0.95,1.0, num=3),
    gamma_range=np.linspace(0.95,1.0, num=3),
    epsilon_range=np.linspace(0.95,1.0, num=3)
)
fig = px.line(optimized_data, x='episode', y='timesteps', color='hyperparameters')
fig.show()
fig = px.line(optimized_data, x='episode', y='rewards', color='hyperparameters')
fig.show()
fig = px.line(optimized_data, x='episode', y='penalties', color='hyperparameters')
fig.show()
fig = px.line(optimized_data, x='episode', y='cost', color='hyperparameters')
fig.show()

/var/folders/h6/9s1mhwcx5zd_n_0bkbfgh6sw0000gn/T/ipykernel_44916/617812815.py:29: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

/var/folders/h6/9s1mhwcx5zd_n_0bkbfgh6sw0000gn/T/ipykernel_44916/617812815.py:29: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

/var/folders/h6/9s1mhwcx5zd_n_0bkbfgh6sw0000gn/T/ipykernel_44916/617812815.py:29: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

/var/folders/h6/9s1mhwcx5zd_n_0bkbfgh6sw0000gn/T/ipykernel_44916/617812815.py:29: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

/var/folders/h6/9s1mhwcx5zd_n_0bkbfgh6sw0000gn/T/ipykernel_44916/617812815.py:29: FutureWarning:

The frame.append method is depreca

   episode  learning_rate  gamma  epsilon  rewards  timesteps  penalties  \
0        0           0.95   0.95     0.95     -164         58         14   
1        1           0.95   0.95     0.95     -257         70         23   
2        2           0.95   0.95     0.95      -18         11          3   
3        3           0.95   0.95     0.95     -132         53         11   
4        4           0.95   0.95     0.95      -92         58          6   

   cost                    hyperparameters  
0   -10  lr=0.95, gamma=0.95, epsilon=0.95  
1   -10  lr=0.95, gamma=0.95, epsilon=0.95  
2   -10  lr=0.95, gamma=0.95, epsilon=0.95  
3   -10  lr=0.95, gamma=0.95, epsilon=0.95  
4   -10  lr=0.95, gamma=0.95, epsilon=0.95  


## Inference

In [14]:
def run_taxi_driver_with_calculated_q_table(
        total_test_ep=TOTAL_TEST_EP,
        max_steps=MAX_STEPS,
        q_table=Q_TABLE
):
    '''
    Run the taxi game with the existing q-table
    :param total_test_ep: Total episodes to run
    :param max_steps: Max steps per episode
    :return:
    '''
    if not np.any(q_table):
        calculate_q_table()

    env.reset()
    rewards = []
    total_rewards_per_ep = []
    total_penalties_per_ep = []
    total_cost_per_ep = []
    total_timesteps_per_ep = []

    for episode in range(total_test_ep):
        state = env.reset()
        step = 0
        done = False
        total_rewards = 0
        total_penalties = 0
        total_timestep = 0
        total_cost = 0

        for step in range(max_steps):

            env.render()

            # Take the action based on the Q Table:
            action = np.argmax(q_table[state, :])

            new_state, reward, done, info = env.step(action)

            total_rewards += reward
            total_timestep += 1

            if reward == -10:
                total_penalties += 1

            if total_rewards < total_cost:
                total_cost = total_rewards

            # If episode finishes:
            if done:
                total_rewards_per_ep.append(total_rewards)
                total_timesteps_per_ep.append(total_timestep)
                total_penalties_per_ep.append(total_penalties)
                total_cost_per_ep.append(total_cost)
                break

            state = new_state
        episode += 1
        
        
    env.close()
    results = pd.DataFrame({
                    'rewards': total_rewards_per_ep,
                    'timesteps':  total_timesteps_per_ep,
                    'penalties':  total_penalties_per_ep,
                    'cost':  total_cost_per_ep,
                })
    # index -> episode
    results = results.reset_index().rename(columns={'index': 'episode'})

    print('Score Over Time: {}'.format(sum(rewards)/total_test_ep))
    fig = px.bar(results, x='episode', y='timesteps')
    fig.show()
    fig = px.bar(results, x='episode', y='rewards')
    fig.show()
    fig = px.bar(results, x='episode', y='penalties')
    fig.show()
    fig = px.bar(results, x='episode', y='cost')
    fig.show()
    
    return results



In [16]:
# r = run_taxi_driver_with_calculated_q_table()
# r.head()

episode  rewards  timesteps  penalties  cost
0        0       12          9          0    -8
1        1        6         15          0   -14
2        2        5         16          0   -15
3        3        5         16          0   -15
4        4        9         12          0   -11

## Program Backend

In [11]:
def user_mode(
    total_ep = TOTAL_EP,
    max_steps = MAX_STEPS,
    lr = LR,
    gamma = GAMMA,
    epsilon = EPSILON,
    max_epsilon = MAX_EPSILON,
    min_epsilon = MIN_EPSILON,
    decay_rate = DECAY_RATE
):
    calculate_q_table(
        total_ep = total_ep,
        max_steps = max_steps,
        lr = lr,
        gamma = gamma,
        epsilon = epsilon,
        max_epsilon = max_epsilon,
        min_epsilon = min_epsilon,
        decay_rate = decay_rate
    )
    run_taxi_driver_with_calculated_q_table()
    pass

def time_mode(steps=TOTAL_TEST_EP):
    run_taxi_driver_with_calculated_q_table(steps)
    pass

## Program Frontend


### Time Mode
Accepts only the number of episodes desired to be run, and the optimized Q-table will be used 

In [17]:
time_mode(
    steps=200
)

+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+

+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (Pickup)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : |_: |
|Y| : |B: |
+---------+
  (North)
+---------+
|R: | : :G|
| : | : : |
| : : :_: |
| | : | : |
|Y| : |B: |
+---------+
  (North)
+---------+
|R: | : :G|
| : | : : |
| : :_: : |
| | : | : |
|Y| : |B: |
+---------+
  (West)
+---------+
|R: | : :G|
| : | : : |
| :_: : : |
| | : | : |
|Y| : |B: |
+---------+
  (West)
+---------+
|R: | : :G|
| :_| : : |
| : : : : |
| | : | : |
|Y| : |B: 

+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (East)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (Pickup)
+---------+
|R: | : :G|
| : | : :_|
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : :_|
| | : | : |
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | :_|
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B:_|
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (West)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+

+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (East)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (East)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |


  (West)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (Pickup)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
|_| : | : |
|Y| : |B: |
+---------+
  (North)
+---------+
|R: | : :G|
| : | : : |
|_: : : : |
| | : | : |
|Y| : |B: |
+---------+
  (North)
+---------+
|R: | : :G|
|_: | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (North)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (North)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+

+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |
|Y| : |B: |
+---------+
  (South)
+---------+
|R: | : :G|
| : | : : |
| : : : : |
| | : | : |

### User Mode
Allows the customization of the parameters to change model functionality

In [ ]:
# user_mode(
#     total_ep=,
#     max_steps=,
#     lr=,
#     gamma=,
#     epsilon=,
#     max_epsilon=,
#     min_epsilon=,
#     decay_rate=
# )



In [ ]:
show_run_stats(rewards_total, penalties_per_ep_total, steps_total, timestep_per_ep_total)